# Import prostředí a výpis verzí PyTorche a Cuda

In [0]:
import os
import torch
from IPython.display import Image, clear_output 
print('PyTorch %s %s' % (torch.__version__, torch.cuda.get_device_properties(0) if torch.cuda.is_available() else 'CPU'))

In [0]:
!git clone https://github.com/roboflow-ai/yolov3  # naklonování yoloV3 pro využití s roboflow

## Získání dat z Roboflow

Při exportování Vybrat možnost "YOLOv3 Darknet" jako formát.

Dále je nutné zakliknout možnost  "show download code", která nám dá možnost stáhnout data přímo z RoboFlow

In [0]:
# Tento link si vygenerujeme v RoboFlow, s nikým jej nesdílejte, protože obsahuje klíč specifický pro každého uživatele.
!curl -L https://app.roboflow.ai/ds/joIfmtbGEE?key=CCghjlqNu0 | jar -x


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100   890  100   890    0     0   1171      0 --:--:-- --:--:-- --:--:--  1169
100 4355k  100 4355k    0     0  4204k      0  0:00:01  0:00:01 --:--:-- 4204k


## Nutná organizace dat z RoboFlow

Musíme rodělit labely a obrázky do dvou patřičných složek.

Následující kód dělá právě to.

In [0]:
 # Vstup do složky train
%cd train

In [0]:
# Vypsání obsahu dané složky
%ls

In [0]:
# Vytvoření složek
%mkdir labels
%mkdir images

In [0]:
# Přesun jednotlivých souborů do korespondujících složek
%mv *.jpg ./images/
%mv *.txt ./labels/

In [0]:
%cd images

In [0]:
# Vytvoření potřebného textového souboru, pro trénování. Obsahuje cesty k labelům a obrázkům
file = open("train_images_roboflow.txt", "w") 
for root, dirs, files in os.walk("."):
    for filename in files:  
      if filename == "train_images_roboflow.txt":
        pass
      else:
        file.write("../train/images/" + filename + "\n")
file.close()

In [0]:
# Vypsání obsahu souboru train_images_roboflow.txt
%cat train_images_roboflow.txt

In [0]:
# Změna složky 
%cd ../../valid

In [0]:
%mkdir labels
%mkdir images

In [0]:
%mv *.jpg ./images/
%mv *.txt ./labels/

In [0]:
%cd images

In [0]:
# Vytvoření textového souboru pro validaci obrázků. 
file = open("valid_images_roboflow.txt", "w") 
for root, dirs, files in os.walk("."):
    for filename in files
      if filename == "valid_images_roboflow.txt":
        pass
      else:
        file.write("../valid/images/" + filename + "\n")
file.close()

In [0]:
%cat valid_images_roboflow.txt

## Konfigurace souborů pro trénování





In [0]:
%cd ../../yolov3/data

/content/yolov3/data


In [0]:
# Výpys souboru, ve kterém jsou uložené naše třídy
%cat ../../train/_darknet.labels

In [0]:
# Převod .labels na .names 
%cat ../../train/_darknet.labels > ../../train/roboflow_data.names

In [0]:
def get_num_classes(labels_file_path):
    classes = 0
    with open(labels_file_path, 'r') as f:
      for line in f:
        classes += 1
    return classes

In [0]:
# Updatování souboru roboflow.data na správný počet tříd
import re
num_classes = get_num_classes("../../train/_darknet.labels")
with open("roboflow.data") as f:
    s = f.read()
with open("roboflow.data", 'w') as f:
    s = re.sub('classes=[0-9]+',
               'classes={}'.format(num_classes), s)
    f.write(s)

In [0]:
# Zobrazí počet tříd
%cat roboflow.data

## Trénování modelu

Trénování defaltně běží na 300 epochů.  


In [0]:
%cd /content/yolov3

In [0]:
# Python kód pro spuštění trénování
!python3 train.py --data data/roboflow.data --epochs 300

## Zobrazení průběhu trénování a uložení vah

Kód níže je defaultně zprostředkovaný skript pro zobrazení průběhu trénování.


In [0]:
from utils import utils; utils.plot_results()

In [0]:
# Uložení natrénovaných vah na lokálním PC
from google.colab import files
files.download('./weights/last.pt')

## Predikce a zobrazení výsledků



### Predikce

Kód  níže predikuje obrázky ze složky test pomocí námi vytrénovaných vah. Tyto predikce uloží do složky output ve složce yolov3.

In [0]:
!python3 detect.py --weights weights/last.pt --source=../test --names=../train/roboflow_data.names

### Zobrazení výsledků na obrázcích
Zobrazení predikcí CNN, které již obsahují bounding boxy vytištěné přimo na jednotlivých obrázcích.

In [0]:
# Import knihoven pro zobrazení výsledků
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from IPython.display import display, Image
from glob import glob
import random
import PIL

In [0]:
# Zobrazení náhodného obrázku ze složky output
filename = random.choice(os.listdir('./output'))
print(filename)
Image('./output/' + filename)

In [0]:
# Zobrazení všech obrázků ze složky output
images = [ PIL.Image.open(f) for f in glob('./output/*') ]

In [0]:
# Uložení natrénovaných vah na lokálním PC
from google.colab import files
files.download('./weights/last.pt')